In [16]:
#pip install -r requirements.txt

In [17]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import nltk
# from nltk.corpus import stopwords
# from nltk.stem import SnowballStemmer
# from nltk.stem import WordNetLemmatizer
import re  
import pickle
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics.pairwise import linear_kernel
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
import matplotlib.pyplot as plt

In [18]:
import nltk
import ssl
 
try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    pass
else:
    ssl._create_default_https_context = _create_unverified_https_context
 
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.stem import SnowballStemmer
stops = set(stopwords.words("english"))
print(stops)


{"haven't", 'themselves', 'she', 'hadn', 'when', 'needn', 'between', "hadn't", 'his', "she's", "wasn't", "you'll", 'all', 'is', 'm', 'some', 'do', 'to', "aren't", 'them', 'him', "it's", 'down', 'until', 'ourselves', "don't", 'over', 'doing', 'were', 'am', 'which', "shan't", 'y', 'aren', 'ain', "shouldn't", "didn't", 'whom', 'and', 'should', "should've", 'about', "hasn't", "you're", 've', 'through', 'below', "you've", "mustn't", 're', 'wasn', 'won', 'same', 'few', 'they', 'itself', 'been', 'the', "wouldn't", 'there', 'again', 'where', 'up', 'each', 'haven', 'of', 'hers', "won't", 'theirs', 'd', 'only', 'so', 'doesn', "that'll", 'having', 'under', 'such', "needn't", 'a', 'out', 'as', 'yours', 'an', 'we', 'did', 'before', 'more', 'for', 'both', 'had', 'most', "doesn't", "weren't", 'our', 'he', 'then', 'you', 'above', 'on', 'will', 'hasn', 'are', 'against', 'didn', 'it', 'couldn', 'no', 'your', 'or', 'into', 'me', 'here', 'be', 'have', 'yourselves', 'just', 'with', "you'd", 'off', 'why', '

[nltk_data] Downloading package stopwords to /u/asitha/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [19]:
import pandas as pd

model_name = "test-data-54000"

df = pd.read_csv(model_name+'.csv')
df.head(10)

key product_l1  \
0   P10237313-17413   10049895   
1  P10049895-134736      Verdi   
2  P10049895-134731      Verdi   
3  P10049895-134730      Verdi   
4  P10049895-134729      Verdi   
5  P10049895-134728      Verdi   
6  P10049895-134727      Verdi   
7  P10049895-134726      Verdi   
8  P10049895-134724      Verdi   
9  P10049895-134717      Verdi   

                                             summary  \
0                [VCF]formal core tgl coverage issue   
1  [VerdiPlay] Migrate VC Apps from Verdi Toolbox...   
2  Empty Box Icon in COV App toolbar in VC Formal...   
3  Empty Box Icon in COV App toolbar in VC Formal...   
4  [Infra][Plato] Change criteria for automatic u...   
5  library search issue in VEGA1 and VEGA2 when u...   
6  enhance the waveform overlapping feature of nW...   
7  Incorrect FSDB generated from VTRAN - FSDB2TB ...   
8   [NPI][VLDB] Extract design with wrong scope type   
9  User can’t identified if Total errors of the d...   

                                         description  
0  Hi Penny  This is the issue reproduced from MT...  
1    Migrate VC Apps from Verdi Toolbox to VerdiPlay  
2  There is an empty box icon in COV app on arm m...  
3  There is an empty box icon in COV app on arm m...  
4  Per our discussion  we would like change the c...  
5  issue specified in this STAR was found during ...  
6  Details of requirements and communications has...  
7  Continuing Jira : P10233201-560      In the VT...  
8  npiProd/src/bin/Apps/VerdiLearn/libvl/model/de...  
9  Issue mentioned in this STAR is found from the...

In [20]:
def view_df(df):
    print(f"Data shape: {df.shape}")
    print("Check for null values:")
    print(df.isnull().sum())
#     print("Check for duplicates:")
#     print(df.is_duplicate.value_counts())
    print(df.head(10))

In [21]:
view_df(df)

Data shape: (54745, 4)
Check for null values:
key            0
product_l1     0
summary        0
description    2
dtype: int64
                key product_l1  \
0   P10237313-17413   10049895   
1  P10049895-134736      Verdi   
2  P10049895-134731      Verdi   
3  P10049895-134730      Verdi   
4  P10049895-134729      Verdi   
5  P10049895-134728      Verdi   
6  P10049895-134727      Verdi   
7  P10049895-134726      Verdi   
8  P10049895-134724      Verdi   
9  P10049895-134717      Verdi   

                                             summary  \
0                [VCF]formal core tgl coverage issue   
1  [VerdiPlay] Migrate VC Apps from Verdi Toolbox...   
2  Empty Box Icon in COV App toolbar in VC Formal...   
3  Empty Box Icon in COV App toolbar in VC Formal...   
4  [Infra][Plato] Change criteria for automatic u...   
5  library search issue in VEGA1 and VEGA2 when u...   
6  enhance the waveform overlapping feature of nW...   
7  Incorrect FSDB generated from VTRAN - FSDB2TB .

In [22]:
# Remove Null data
df.dropna(inplace=True)
view_df(df)

Data shape: (54743, 4)
Check for null values:
key            0
product_l1     0
summary        0
description    0
dtype: int64
                key product_l1  \
0   P10237313-17413   10049895   
1  P10049895-134736      Verdi   
2  P10049895-134731      Verdi   
3  P10049895-134730      Verdi   
4  P10049895-134729      Verdi   
5  P10049895-134728      Verdi   
6  P10049895-134727      Verdi   
7  P10049895-134726      Verdi   
8  P10049895-134724      Verdi   
9  P10049895-134717      Verdi   

                                             summary  \
0                [VCF]formal core tgl coverage issue   
1  [VerdiPlay] Migrate VC Apps from Verdi Toolbox...   
2  Empty Box Icon in COV App toolbar in VC Formal...   
3  Empty Box Icon in COV App toolbar in VC Formal...   
4  [Infra][Plato] Change criteria for automatic u...   
5  library search issue in VEGA1 and VEGA2 when u...   
6  enhance the waveform overlapping feature of nW...   
7  Incorrect FSDB generated from VTRAN - FSDB2TB .

In [23]:
# Create corpus from data frame
corpus = df.to_dict('records')
#print(corpus[0:5])

In [24]:
def clean_text(text, remove_stopwords=True):
    # Clean the text, with the option to remove stopwords.
    
    # Convert words to lower case and split them
    words = text.lower().split()

    # Optionally remove stop words (true by default)
    if remove_stopwords:
        stops = set(stopwords.words("english"))
        words = [w for w in words if not w in stops]
    
    cleaned_text = " ".join(words)

    # Clean the text
    cleaned_text = re.sub(r"[^A-Za-z0-9(),!.?\'\`]", " ", cleaned_text)
    cleaned_text = re.sub(r"\'s", " 's ", cleaned_text)
    cleaned_text = re.sub(r"\'ve", " 've ", cleaned_text)
    cleaned_text = re.sub(r"n\'t", " 't ", cleaned_text)
    cleaned_text = re.sub(r"\'re", " 're ", cleaned_text)
    cleaned_text = re.sub(r"\'d", " 'd ", cleaned_text)
    cleaned_text = re.sub(r"\'ll", " 'll ", cleaned_text)
    cleaned_text = re.sub(r",", " ", cleaned_text)
    cleaned_text = re.sub(r"\.", " ", cleaned_text)
    cleaned_text = re.sub(r"!", " ", cleaned_text)
    cleaned_text = re.sub(r"\(", " ( ", cleaned_text)
    cleaned_text = re.sub(r"\)", " ) ", cleaned_text)
    cleaned_text = re.sub(r"\?", " ", cleaned_text)
    cleaned_text = re.sub(r"\s{2,}", " ", cleaned_text)
    
    words = re.split('\W+', cleaned_text)                        # remove all non-words (make a list)
#     words = cleaned_text.split()
    
    # Shorten words to their stems
    stemmer = SnowballStemmer('english')
    stemmed_words = [stemmer.stem(word) for word in words]
    
    cleaned_text = " ".join(stemmed_words)
    
    # Return cleaned text 
    return(cleaned_text)

# test clean_text
#_text="Verdi issue : stop cmd is not getting triggered when there is change in event"
#print(clean_text(_text))

In [25]:
# Input: corpus is a list of dictionaries(with all fields and data) 
def extract_clean_documents_from_corpus(corpus):
    print("Extracting and Cleaning documents...")
    final_corpus = []
    list_of_docs = []
    i = 0
    for ticket_dict in corpus:
        print("Processing ",ticket_dict['summary'])
        doc_cleaned_text = ''
        document_of_words = (str(ticket_dict['summary'])+" "+str(ticket_dict['description']))
#         document_of_words = (str(ticket_dict['question1']))
        doc_cleaned_text = clean_text(document_of_words)
        list_of_docs.append(doc_cleaned_text)
        final_corpus.append({'key':ticket_dict['key'],'index':i})
#         final_corpus.append({'qid1':ticket_dict['qid1'], 'words':doc_cleaned_text, 'index':i})
        i+=1
    return list_of_docs,final_corpus



In [26]:
# extract_clean_documents_from_corpus
list_of_docs,training_ticket_corpus = extract_clean_documents_from_corpus(corpus)

Extracting and Cleaning documents...
Processing  [VCF]formal core tgl coverage issue
Processing  [VerdiPlay] Migrate VC Apps from Verdi Toolbox to VerdiPlay
Processing  Empty Box Icon in COV App toolbar in VC Formal ARM/GV2 on AWS
Processing  Empty Box Icon in COV App toolbar in VC Formal ARM/GV2 on AWS
Processing  [Infra][Plato] Change criteria for automatic update plato label
Processing  library search issue in VEGA1 and VEGA2 when using `uselib  
Processing  enhance the waveform overlapping feature of nWave GUI
Processing  Incorrect FSDB generated from VTRAN - FSDB2TB config
Processing  [NPI][VLDB] Extract design with wrong scope type
Processing  User can’t identified if Total errors of the design greater than Max mismatch entry defined in rca.yaml when run DUTRCA
Processing  CLONE - Apple: SDC instance name: VC support for "use_generate_separator" SG option
Processing  Wrong Layer/PermName annotation of parameters retrieved by testkdb in spicom_gb 
Processing  Verdi hang when selec

Processing  DSL extension support
Processing  Intel-GT-VCPS: Verdi PSS window: Remove "M" & "F" suffix in Instance tree items  make them DSL constructs based  not Verilog
Processing  enable sync action selection in “PSS Action view” to solution graph on by default
Processing  [VPSG] Fix look and feel issues
Processing  Need for Solution Analyzer similar to activity Analyzer 
Processing  Solution Graph: Add new pane for resource objects and show which action use
Processing  Provide better visibility to attributes in action waveform  we missing resource and flow-object information
Processing  object instance should refer to all instantiation source location
Processing  brand Simulator and dumper info on PSS action fsdb
Processing  Action waveform - Provide different streams for different executor instances
Processing  Synchronization between Activity  solution graph and source code.
Processing  Improve message in Verdi Dialog box 
Processing  Solution Graph Expand/Collapse all
Processing

Processing  [VPSG] Display struct type in type filed of struct 
Processing  [VPSG] Fix solution graph issues
Processing  [PSS] solution database will not be invoked if compile database invoke fail
Processing  [VPSG] Search node to enter into the collapsed compound action
Processing  [VPSG] comp_id should be comp  type should be component 
Processing  [PSS] partial buffer node will not be displayed in pss solution graph 
Processing  Solution Graph: Difficult to control zoom/zoom out and scrolling  most probably a scrolling bar is needed  or some layout stability
Processing  [PSS] solution graph can be enable in SX mode
Processing  [PSS] member view will not show the int type variable
Processing  [VPSG]Empty directory should report error messages
Processing  [PSS][NewAPI] "test" option is not work 
Processing  [VPSG] Enum value is displayed as number  not enum item
Processing  Source file not found from transaction debug right click to get source file
Processing  duplicated edge after mu

Processing  [QLPAC+Save_Restore]:[-restore] iso/ret cells are missing in schematic during restore when "set_app_var enable_vcf_lpcc_kdb true" is disabled
Processing  Ports listed in VERDI “Power State Table” and “nWave” are wrong
Processing  [QLPAC+Save_Restore]:iso/ret cells are missing in schematic during restore when "set_app_var enable_vcf_lpcc_kdb true" is enabled
Processing  [QLPAC+Save_Restore]:KDB Error during restore when "set_app_var enable_vcf_lpcc_kdb true" is disabled
Processing  [QLPAC+Save_Restore]:KDB Error during restore when "set_app_var enable_vcf_lpcc_kdb true" is enabled
Processing  [QLPAC+Save_Restore]:Instance hierarcy pane is empty  when "set_app_var enable_vcf_lpcc_kdb true" is enabled
Processing  [Verdi_forces] :  discrepancy between  fsdbreport and zwdutils
Processing  [Intel-SDG-10nm] [VEGA2] mesh: Vega2 kdb dumping memory increase
Processing  Verdi VCS inconsistency in handling config setup
Processing  [SDB] Hierarchy Tree Builder for Path Compression
Proce

Processing  update release notes of Verdi 2020.12-SP1 to list support of Xcelium 20.09
Processing  [SmartLog] Refine partition rule config dialog
Processing  CLONE - Incorrect selected net name in the schematic with DNR for the provided scenario
Processing  Request for dumping `define values into fsdb
Processing  FVLP_CC : need a way to show src signal for PG-pin property  
Processing  FVLP_CC :  src and dest pointing to same net when they are UPF objects 
Processing  [UpwardTrack] Not set start point with preference disable "Hide Block Not Matching Search"
Processing  QCOM : Constraint Command  details in property window
Processing  [FSDB Writer] Memory reduced MDA dumping support 
Processing  CLONE - VHDL08 resolution indication does not work if the type is not in active scope
Processing  CLONE - VHDL08 resolution indication does not work for types defined outside package
Processing  User experience issue at startup with Verdi GUI opening for a short time in AWS SOCA
Processing  Pote

...

Processing  [QACG] ] No way to close el file which we have loaded
Processing  [tBrowser] Highlight stream if the stream contains expected value/error message
Processing  [tAnalyzer] Search support for expected value / error message
Processing  [QA][Smart Log] Should pop-up warning dialog to tell no response of hyperli
Processing  [Verdi][Coverage] enhance the hyper-link rule by support file:// and ftp
Processing  [Verdi][Coverage] cannot show hyper-link when HvpDetail in view mode
Processing  One temporal limitation of unified spice script flow in 2015.09
Processing  DVE mode choice in Verdi GUI
Processing  Streamlined consistency check (checksum issue)
Processing  [VC Apps][Lang][L0][VHDL] Known defects of NPI VHDL Model
Processing  [Identify search] Verdi Fast Global Search Support - RMB for interactive debug
Processing  [Identify search] Verdi Fast Global Search Support - GUI range/multiple select
Processing  Enabling strength recording for FSDB disables FsdbGates optimizations.
Pro

Processing  SpecLinking: remembering selections for sections after undo/redo
Processing  fsdbmerge support transaction based FSDB
Processing  fsdbextract support transaction based FSDB
Processing  Transaction dumping support auto switch
Processing  Transaction Windows support auto update
Processing  UVM-aware Windows support incomplete transaction data
Processing  Transaction Windows support incomplete transaction data
Processing  use VCS unnamed gen-block as default mode in simflow
Processing  nWave signal hierachical name alignment.
Processing  [VC Apps][DM][L0] DM model support VHDL - Traverse Operation / Statement
Processing  Avago - Verdi coverage gui - error saving plan
Processing  spec-link order to multiple features
Processing  subplan creation too many clicks
Processing  [DA] daSignalTest::from_MSE_237862
Processing  Qcom-RTP:Hawker: uvm1.1d verdi instrumentation needed
Processing  [nWave] refine Get Signal Form (unfinished parts)
Processing  [VC Apps][Lang][L1] New API: npi_u

Processing  Add C API for stream attribute for new format transaction
Processing  enhance verdi env stdout help
Processing  on-demand grading based on user-selected coverage objects
Processing  prompt user to reload new coverage results when .vdb changes
Processing  remember users settings in the tools->run tests dialog
Processing  Pop-up warning when verdi compilation failed
Processing  [RDLPI] Support merged cell for structure signal
Processing  FSDB Dumping Command for Synopsys (vcs) usages need to modify in document
Processing  [HDB][DL] Increase the DL performance for pass-through
Processing  FSDB dumping >2hrs reduced to 10mins due to incorrect setup. needs to be >10mins
Processing  [TFV] Refine the description of "Trace Unknown Power State"
Processing  [Interconnect] Semantics checking for interconnect connection
Processing  [Verdi3][nWave] Comparison issue for one special VHDL fsdb from user
Processing  Verdi should not allow sim to run if the Verdi compile fails
Processing  mi

Processing  [QAiSim1307][Constraint] Support Delete key in Relation Pane
Processing  [Verdi][Coverage] User cannot save the adjust of column of HVP
Processing  Autocompletion in TCLcommand window in Verdi
Processing  [SV2012][nTrace] Support type resolve for modport expression
Processing  All nWave dialog boxes forget their last position on next Verdi invocation
Processing  [Verdi3] nSchema could not trace driver of external reference to interface
Processing  Re-design nWave's Open File dialog by Qt widgets
Processing  Planner needs to support multiple VDBs (-featurefile)
Processing  Prompt users to save merged DBs before quitting
Processing  VCRM: incorporate a subplan from NLP in planner
Processing  [QAiSim1403] no function return value on local pane
Processing  [Verdi3][GUI] support new max spec with tabified docked widget/window
Processing  Font Size Preference
Processing  Allow users to mark a coverage item as unimplemented in a plan
Processing  Need a single toggle button to Enab

Processing  customer would like to select and copy delta time
Processing  (F case) searching for instance using filter in hierarchy browser hangs Verdi
Processing  [Transaction Recording] Improve the hooks function performance
Processing  [Verdi][Coverage] Help->Bookshelf can't work
Processing  [nWave][getSignalForm] performance when scroll which trigger treeAskChildrenCBS
Processing  [QAiSim1403][CSI3][Local Pane] user defined type function argument is missing
Processing  [FSDB] support write value pattern into reader buffer (runtime signal)
Processing  [QAVIP][SrcProt][nTrace] nText cannot fold decrypted code
Processing  [Verdi][Coverage] D&D covergroup/coverpoint from Verdi to VdCov can't work
Processing  [Transaction Debug][VIP] Convert PA XML file into transaction based FSDB
Processing  New utility which support Trace ActiveX in batch m
Processing  Listing out simulator forced signals in the Verdi-FSDB --- Solution in AP
Processing  Allow qwAddMenuAction to create action in top me

In [27]:
#save and load moddel
def save_model(model,model_name):
    pickle.dump(model, open(model_name, "wb"))

def load_model(model_file_path):
    with open(model_file_path, 'rb') as pickled_file:
        loaded_model_data = pickle.load(pickled_file)
    return loaded_model_data

In [32]:
# Train the model
tfidf_model = TfidfVectorizer()

tfidf_trainingset = tfidf_model.fit_transform(list_of_docs)

save_model(tfidf_trainingset,model_name+".pickle")
save_model(training_ticket_corpus,model_name+"_corpus.pickle")

Load models and get result

In [33]:
def find_top_n_similar_documents(n,tfidf_test,tfidf_trainingset,cleaned_training_corpus):
    cosine_similarities = linear_kernel(tfidf_test, tfidf_trainingset).flatten()
    related_docs_indices = cosine_similarities.argsort()[:-n:-1]
    related_jira_ids = []
    for ticket in cleaned_training_corpus:
        if(ticket['index'] in related_docs_indices):
            related_jira_ids.append(ticket['key'])
#             related_jira_ids.append(ticket['qid1'])
    return related_docs_indices,related_jira_ids

In [34]:

my_model = load_model(model_name+".pickle")
my_corpus = load_model(model_name+"_corpus.pickle")

tickets_dev_set = corpus[0:5]

for ticket in tickets_dev_set:
    
    document_test = (str(ticket['summary'])+" "+str(ticket['description']))
    cleaned_document = clean_text(document_test)
    cleaned_document = [cleaned_document]
    tfidf_test = tfidf_model.transform(cleaned_document)
    related_indices, related_jiras = find_top_n_similar_documents(6,tfidf_test[0:1],my_model,my_corpus)
    print("\n",ticket['key'],">>>> \n",related_jiras,"\n")


 P10237313-17413 >>>> 
 ['P10237313-17413', 'P10049895-47090', 'P10049895-42992', 'P10049895-13239', 'P10049895-12837'] 


 P10049895-134736 >>>> 
 ['P10049895-134736', 'P10049895-122845', 'P10049895-119678', 'P10049895-50955', 'P10049895-48496'] 


 P10049895-134731 >>>> 
 ['P10049895-134731', 'P10049895-134730', 'P10049895-122997', 'P10049895-25562', 'P10049895-7156'] 


 P10049895-134730 >>>> 
 ['P10049895-134731', 'P10049895-134730', 'P10049895-122997', 'P10049895-25562', 'P10049895-7156'] 


 P10049895-134729 >>>> 
 ['P10049895-134729', 'P10049895-132883', 'P10049895-37563', 'P10049895-37115', 'P10049895-8035'] 



In [ ]:
print(tfidf_test)